In [1]:
"""This notebook is written to parse the new Octant.IO dataset and extract basic statistics on the scenes."""

import os
import sys
import multiprocessing
import pandas as pd
import matplotlib.pyplot as plt
plt.switch_backend('TkAgg')
import time
import csv
import re

from tqdm import tqdm
import matplotlib.cm as cm
import numpy as np
from PIL import Image
import glob

# location analysis
from urllib2 import urlopen
import json
# !{sys.executable} -m pip install geopy



In [2]:
# GPS localization imports
# !{sys.executable} -m pip install folium
import requests
from xml.etree import ElementTree
import folium

/home/an/anaconda2/lib/python2.7/site-packages/folium/__init__.py:59: UserWarning: This version of folium is the last to support Python 2. Transition to Python 3 to be able to receive updates and fixes. Check out https://python3statement.org/ for more info.
  UserWarning


In [346]:
!{sys.executable} -m pip install opencage

DEPRECATION: Python 2.7 will reach the end of its life on January 1st, 2020. Please upgrade your Python as Python 2.7 won't be maintained after that date. A future version of pip will drop support for Python 2.7.
  Stored in directory: /home/an/.cache/pip/wheels/d4/e8/a7/9ab10a0e19d854df7fe84e58529f45081703389c171c9eac08
Successfully built opencage


In [52]:
!{sys.executable} -m pip install statistics

DEPRECATION: Python 2.7 will reach the end of its life on January 1st, 2020. Please upgrade your Python as Python 2.7 won't be maintained after that date. A future version of pip will drop support for Python 2.7.
  Stored in directory: /home/an/.cache/pip/wheels/75/55/90/73aa7662bfb4565b567618547a275f01372a678ca92ecd64f3
Successfully built statistics


In [10]:
from folium.plugins import MarkerCluster
from geopy.geocoders import GoogleV3
from geopy.geocoders import Nominatim
from opencage.geocoder import OpenCageGeocode
from statistics import median, mean

In [3]:
# get filepath of octant.io dataset
filepath = "/home/an/work/cyngn/data/octant.io/csv/"
os.chdir(filepath)

In [60]:
# combine all csv metadata files into one csv file: combined_csv
extension = 'csv'
all_filenames = [i for i in glob.glob('*.{}'.format(extension))]

# combine all files in the list
combined_csv = pd.concat([pd.read_csv(f) for f in all_filenames ])

# export to csv
combined_csv.to_csv("combined_csv.csv", index=False, encoding='utf-8-sig')

In [4]:
# read and display combined csv
df = pd.read_csv("combined_csv.csv") 
df.head(5)

filename  driver_id  video_time(s)  \
0  dawn_or_dusk-snowy-suburban-00001.mov         61              0   
1  dawn_or_dusk-snowy-suburban-00001.mov         61              1   
2  dawn_or_dusk-snowy-suburban-00001.mov         61              2   
3  dawn_or_dusk-snowy-suburban-00001.mov         61              3   
4  dawn_or_dusk-snowy-suburban-00001.mov         61              4   

          gps_date_time        gps_latitude        gps_longitude  \
0  2018:11:15 21:09:03Z  40 deg 41' 3.99" N  73 deg 51' 41.85" W   
1  2018:11:15 21:09:04Z  40 deg 41' 4.05" N  73 deg 51' 41.81" W   
2  2018:11:15 21:09:05Z  40 deg 41' 4.11" N  73 deg 51' 41.75" W   
3  2018:11:15 21:09:06Z  40 deg 41' 4.17" N  73 deg 51' 41.67" W   
4  2018:11:15 21:09:07Z  40 deg 41' 4.23" N  73 deg 51' 41.57" W   

   gps_speed(km/h)  
0            7.092  
1            8.568  
2            9.108  
3           10.152  
4           10.296

In [62]:
# # driver ID distribution
# fig = df.groupby(["driver_id"]).size().plot.bar(x = 'Driver ID', y= "# of samples")

# for p in fig.patches:
#     fig.annotate(str(p.get_height()), (p.get_x(), p.get_height()), horizontalalignment='center', fontsize=5)

# fig.get_figure().savefig("/home/an/work/cyngn/data/octant.io/plots/" + "fig1", dpi=500)

In [63]:
# # driver ID distribution
# ax = df.groupby(["driver_id"]).size().plot.bar()

# plt.ylabel("# of samples")
# plt.xlabel("driver ID")

# for p in ax.patches:
#     ax.annotate(str(p.get_height()), (p.get_x() * 1.005, p.get_height() * 1.005))
    
# ax.get_figure().savefig("/home/an/work/cyngn/data/octant.io/plots/" + "fig1", dpi=500, format='png', bbox_inches='tight')

In [5]:
# dataset size statistics
# get number of unique samples in combined csv file
row_count = len(df.index)
print("# of samples: ", row_count)

('# of samples: ', 197364)


In [6]:
# get total number of unique clips in combined csv file (see length at end)
pd.options.display.max_rows = 20
df.groupby(["filename"]).size()

SyntaxError: invalid syntax (<ipython-input-6-dfe34a48a43b>, line 3)

In [66]:
# scene statistics
# dictionaries keeping track of the number of scenes, clips, and samples for each subcategory in lighting, weather, and scenery
lighting_scene = {'none': 0}
weather_scene = {'none': 0}
scenery_scene = {'none': 0}

lighting_clip = {'none': 0}
weather_clip = {'none': 0}
scenery_clip = {'none': 0}

lighting_sample = {'none': 0}
weather_sample = {'none': 0}
scenery_sample = {'none': 0}

for csv in os.listdir(filepath):
    data = pd.read_csv(csv)
    sample_count = len(data.index)
    clip_count = len(data.groupby(["filename"]).size())
    title = csv[14:len(csv)-4]
    new_title = re.split(r'[\s-]+', title)
    
    if len(new_title) == 1:
        continue
        
    if len(new_title) == 2:
        lighting_scene['none'] += 1
        weather_scene['none'] += 1
        lighting_clip['none'] += clip_count
        weather_clip['none'] += clip_count
        lighting_sample['none'] += sample_count
        weather_sample['none'] += sample_count
        if new_title[1] not in scenery_sample:
            scenery_scene[new_title[1]] = 0
            scenery_clip[new_title[1]] = 0
            scenery_sample[new_title[1]] = 0
        scenery_scene[new_title[1]] += 1
        scenery_clip[new_title[1]] += clip_count
        scenery_sample[new_title[1]] += sample_count
        continue
    
    if new_title[1] not in lighting_sample:
        lighting_scene[new_title[1]] = 0
        lighting_clip[new_title[1]] = 0
        lighting_sample[new_title[1]] = 0
    lighting_scene[new_title[1]] += 1
    lighting_clip[new_title[1]] += clip_count
    lighting_sample[new_title[1]] += sample_count
    
    if new_title[2] not in weather_sample:
        weather_scene[new_title[2]] = 0
        weather_clip[new_title[2]] = 0
        weather_sample[new_title[2]] = 0
    weather_scene[new_title[2]] += 1
    weather_clip[new_title[2]] += clip_count
    weather_sample[new_title[2]] += sample_count
    
    if new_title[3] not in scenery_sample:
        scenery_scene[new_title[3]] = 0
        scenery_clip[new_title[3]] = 0
        scenery_sample[new_title[3]] = 0
    scenery_scene[new_title[3]] += 1
    scenery_clip[new_title[3]] += clip_count
    scenery_sample[new_title[3]] += sample_count

print("number of scenes")
print(lighting_scene)
print(weather_scene)
print(scenery_scene)
    
print("number of clips")
print(lighting_clip)
print(weather_clip)
print(scenery_clip)

print("\nnumber of samples")
print(lighting_sample)
print(weather_sample)
print(scenery_sample)

number of scenes
{'none': 1, 'day': 49, 'dawn_or_dusk': 42, 'night': 28}
{'none': 1, 'snowy': 21, 'clear': 7, 'overcast': 14, 'sunny': 14, 'heavy_rain': 21, 'partly_cloudy': 14, 'light_rain': 21, 'foggy': 7}
{'country_side': 17, 'none': 0, 'gas_station': 17, 'tunnel': 1, 'suburban': 17, 'forest_road': 17, 'city_center': 17, 'parking_lot': 17, 'highway': 17}
number of clips
{'none': 436, 'day': 5960, 'dawn_or_dusk': 444, 'night': 2590}
{'none': 436, 'snowy': 486, 'clear': 2041, 'overcast': 958, 'sunny': 1952, 'heavy_rain': 471, 'partly_cloudy': 1949, 'light_rain': 877, 'foggy': 260}
{'country_side': 959, 'none': 0, 'gas_station': 188, 'tunnel': 436, 'suburban': 1430, 'forest_road': 470, 'city_center': 3372, 'parking_lot': 292, 'highway': 2283}

number of samples
{'none': 9139, 'day': 124765, 'dawn_or_dusk': 9255, 'night': 54205}
{'none': 9139, 'snowy': 10196, 'clear': 42689, 'overcast': 20059, 'sunny': 40844, 'heavy_rain': 9868, 'partly_cloudy': 40788, 'light_rain': 18355, 'foggy': 5426

In [332]:
# driver ID analysis
# get number of samples associated with each driver ID
pd.options.display.max_rows = 100
df.groupby(["driver_id"]).size()

driver_id
6       1323
13      1050
17      1405
19      2338
21      2380
22      1182
23      1300
25       819
29      2527
31      4024
32      3402
33      1468
35      1343
37      4480
39      7862
41      1069
43      2788
45      3926
47      4554
48      1322
59       356
61     47152
63      1217
65      5289
67      1667
69     11091
75       209
87      3589
89     15933
91      7417
95      3414
96       231
97      4710
103     7128
105     1573
107    34675
109     1151
dtype: int64

In [68]:
# df.groupby(["gps_date_time"]).size()
pd.options.display.max_rows = 40
# number of unique days of filming
df.groupby([df.gps_date_time.str[:4], df.filename]).size()

gps_date_time  filename                                     
2017           dawn_or_dusk-heavy_rain-forest_road-00003.mov    21
               dawn_or_dusk-heavy_rain-suburban-00002.mov       21
               dawn_or_dusk-heavy_rain-suburban-00003.mov       21
               dawn_or_dusk-light_rain-city_center-00003.mov    21
               dawn_or_dusk-light_rain-city_center-00004.mov    21
               dawn_or_dusk-light_rain-city_center-00005.mov    21
               dawn_or_dusk-light_rain-city_center-00006.mov    21
               dawn_or_dusk-light_rain-city_center-00007.mov    21
               dawn_or_dusk-light_rain-forest_road-00003.mov    21
               dawn_or_dusk-light_rain-highway-00001.mov        21
               dawn_or_dusk-light_rain-highway-00002.mov        21
               dawn_or_dusk-light_rain-highway-00007.mov        21
               dawn_or_dusk-light_rain-highway-00008.mov        21
               dawn_or_dusk-light_rain-highway-00011.mov        21
 

In [69]:
# date and time statistics
# number of unique hours of filming
df.groupby(df.gps_date_time.str[10:13]).size()

gps_date_time
 00     9125
 01     7804
 02     7643
 03     5568
 04     4239
 05     4161
 06     2173
 07     1062
 08      491
 09     1114
 10      985
 11     2651
 12     3450
 13     4987
 14     8561
 15    11148
 16    13541
 17    18567
 18    16872
 19    15978
 20    14695
 21    14509
 22    16021
 23    12019
dtype: int64

In [70]:
# number of unique months of filming
df.groupby(df.gps_date_time.str[5:7]).size()

gps_date_time
01     8493
02    14988
03    15597
04     7733
05     7984
06     7151
07    16623
08    23163
09    25187
10    26793
11    25486
12    18166
dtype: int64

In [71]:
# number of unique days of filming
df.groupby(df.gps_date_time.str[:10]).size()

gps_date_time
2017:07:05    189
2017:07:06    105
2017:07:07    272
2017:07:08     78
2017:07:09     21
2017:07:11    290
2017:07:12    168
2017:07:13     84
2017:07:14    210
2017:07:15     21
2017:07:16     84
2017:07:17    378
2017:07:18    483
2017:07:19     42
2017:07:20    168
2017:07:22    189
2017:07:23     21
2017:07:24    419
2017:07:26     21
2017:07:27    147
             ... 
2019:03:22    315
2019:03:23    105
2019:03:24     21
2019:03:26    189
2019:03:27    189
2019:03:28    105
2019:03:29     84
2019:04:01     42
2019:04:02     21
2019:04:03    210
2019:04:04     41
2019:04:05    126
2019:04:06    335
2019:04:08     40
2019:04:09     42
2019:04:11    126
2019:04:12    104
2019:04:15    209
2019:05:24    546
2019:05:29    504
Length: 558, dtype: int64

In [72]:
# number of unique years of filming
df.groupby(df.gps_date_time.str[:4]).size()

gps_date_time
2017     45071
2018    134889
2019     17404
dtype: int64

In [73]:
# number of unique MM/YY of filming
df.groupby(df.gps_date_time.str[:7]).size()

gps_date_time
2017:07     3662
2017:08     6640
2017:09    13423
2017:10     9380
2017:11     5007
2017:12     6959
2018:01       21
2018:02    12829
2018:03    11170
2018:04     6437
2018:05     6934
2018:06     7151
2018:07    12961
2018:08    16523
2018:09    11764
2018:10    17413
2018:11    20479
2018:12    11207
2019:01     8472
2019:02     2159
2019:03     4427
2019:04     1296
2019:05     1050
dtype: int64

In [8]:
# GPS visualization
# number of unique hours of filming
latitudes = df.groupby(df.gps_latitude.str[:]).size()
# longitudes = df.groupby(df.gps_longitude.str[:]).size()
df.head()

filename  driver_id  video_time(s)  \
0  dawn_or_dusk-snowy-suburban-00001.mov         61              0   
1  dawn_or_dusk-snowy-suburban-00001.mov         61              1   
2  dawn_or_dusk-snowy-suburban-00001.mov         61              2   
3  dawn_or_dusk-snowy-suburban-00001.mov         61              3   
4  dawn_or_dusk-snowy-suburban-00001.mov         61              4   

          gps_date_time        gps_latitude        gps_longitude  \
0  2018:11:15 21:09:03Z  40 deg 41' 3.99" N  73 deg 51' 41.85" W   
1  2018:11:15 21:09:04Z  40 deg 41' 4.05" N  73 deg 51' 41.81" W   
2  2018:11:15 21:09:05Z  40 deg 41' 4.11" N  73 deg 51' 41.75" W   
3  2018:11:15 21:09:06Z  40 deg 41' 4.17" N  73 deg 51' 41.67" W   
4  2018:11:15 21:09:07Z  40 deg 41' 4.23" N  73 deg 51' 41.57" W   

   gps_speed(km/h)  
0            7.092  
1            8.568  
2            9.108  
3           10.152  
4           10.296

In [9]:
# function to convert degrees minutes seconds coordinates (DMS) to decimal degrees
def dms2dd(s):
    # example: s = """## deg ##' ##.##" L"""
    degrees, deg, minutes, seconds, direction = re.split(r'[\s-]+', s)
    dd = float(degrees) + float(minutes[:len(minutes)-1])/60 + float(seconds[:len(seconds)-1])/(60*60);
    if direction in ('S','W'):
        dd*= -1
    return dd

gps_df = df[['gps_latitude', 'gps_longitude']].copy()

gps_df['gps_latitude'] = gps_df['gps_latitude'].apply(dms2dd)
gps_df['gps_longitude'] = gps_df['gps_longitude'].apply(dms2dd)

print(gps_df)

        gps_latitude  gps_longitude
0          40.684442     -73.861625
1          40.684458     -73.861614
2          40.684475     -73.861597
3          40.684492     -73.861575
4          40.684508     -73.861547
5          40.684519     -73.861519
6          40.684533     -73.861489
7          40.684544     -73.861453
8          40.684553     -73.861422
9          40.684561     -73.861392
10         40.684569     -73.861367
11         40.684578     -73.861342
12         40.684583     -73.861319
13         40.684589     -73.861297
14         40.684592     -73.861283
15         40.684594     -73.861275
16         40.684594     -73.861272
17         40.684594     -73.861269
18         40.684594     -73.861269
19         40.684594     -73.861269
20         40.684592     -73.861267
21         40.680258     -73.859758
22         40.680258     -73.859758
23         40.680258     -73.859758
24         40.680261     -73.859758
25         40.680267     -73.859758
26         40.680281     -73

In [11]:
latitudes = gps_df["gps_latitude"].tolist()
longitudes = gps_df["gps_longitude"].tolist()
count = 0


map = folium.Map(location=[latitudes[0], longitudes[0]], tiles='CartoDB dark_matter', zoom_start=12)
marker_cluster = MarkerCluster().add_to(map)

for i in range(0, len(latitudes), 21):
    count += 1
    folium.Marker([latitudes[i], longitudes[i]]).add_to(marker_cluster)
map

In [8]:
print(count)

9399


In [118]:
map2 = folium.Map(location=[latitudes[0], longitudes[0]], tiles='CartoDB dark_matter', zoom_start=12)
marker_cluster = MarkerCluster().add_to(map2)

for i in range(len(latitudes)/2, len(latitudes), 21):
    count += 1
    folium.Marker([latitudes[i], longitudes[i]]).add_to(marker_cluster)
map2

In [63]:
# location analysis
# function to get the city name from latitude and longitude coordinates

latitudes = gps_df["gps_latitude"].tolist()
longitudes = gps_df["gps_longitude"].tolist()

print(len(latitudes))

# key = 'afcaccdf147b4b0fb9895f525936d685'
# geocoder = OpenCageGeocode(key)

# cities = []
# for i in range(0, len(latitudes), 21):
#     results = geocoder.reverse_geocode(latitudes[i], longitudes[i])
#     try:
#         print(results[0]['components']['city'] + ", " + results[0]['components']['state'])
#         cities.append(results[0]['components']['city'] + ", " + results[0]['components']['state'])
#     except:
#         continue

# city_dict = {}
# for city in cities:
#     if city not in city_dict:
#         city_dict[city] = 0
#     city_dict[city] += 1

# print(city_dict)

NameError: name 'gps_df' is not defined

In [29]:
# individual driver statistics (61, 107, 89)
df_copy = df.copy()
df_61 = pd.DataFrame(df_copy[df_copy.driver_id == 61])
df_107 = pd.DataFrame(df_copy[df_copy.driver_id == 107])
df_89 = pd.DataFrame(df_copy[df_copy.driver_id == 89])

df_107.head()

filename  driver_id  video_time(s)  \
168  day-overcast-forest_road-00006.mov        107              0   
169  day-overcast-forest_road-00006.mov        107              1   
170  day-overcast-forest_road-00006.mov        107              2   
171  day-overcast-forest_road-00006.mov        107              3   
172  day-overcast-forest_road-00006.mov        107              4   

            gps_date_time         gps_latitude        gps_longitude  \
168  2018:07:25 21:51:21Z  43 deg 36' 47.56" N   70 deg 21' 9.59" W   
169  2018:07:25 21:51:22Z  43 deg 36' 47.56" N   70 deg 21' 9.59" W   
170  2018:07:25 21:51:23Z  43 deg 36' 47.56" N   70 deg 21' 9.59" W   
171  2018:07:25 21:51:24Z  43 deg 36' 46.12" N  70 deg 21' 11.61" W   
172  2018:07:25 21:51:25Z  43 deg 36' 45.70" N  70 deg 21' 12.07" W   

     gps_speed(km/h)  
168            0.000  
169            0.000  
170            0.000  
171           58.248  
172           58.788

In [274]:
# date and time statistics
# number of unique hours of filming
df_89.groupby(df_89.gps_date_time.str[10:13]).size()

gps_date_time
 00     231
 01      42
 02      42
 05      42
 06      21
 07      21
 08      42
 09      42
 10      84
 11     703
 12    1016
 13    1066
 14     907
 15     839
 16    1252
 17    2885
 18    1533
 19    1008
 20     920
 21    1137
 22    1302
 23     798
dtype: int64

In [ ]:
# number of unique months of filming
df_61.groupby(df_61.gps_date_time.str[5:7]).size()

In [278]:
# number of unique days of filming
df_89.groupby(df_89.gps_date_time.str[:10]).size()

gps_date_time
2017:08:26      63
2017:08:29      21
2017:09:01     168
2017:09:02      84
2017:09:05     294
2017:09:06     273
2017:09:07     273
2017:09:08     294
2017:09:09     189
2017:09:11     102
2017:09:12     273
2017:09:13     315
2017:09:14      84
2017:09:15     189
2017:09:16      42
2017:09:18      63
2017:09:19     105
2017:09:20      63
2017:09:22     231
2017:09:23     105
              ... 
2017:11:22     336
2017:11:27     210
2017:11:28     263
2017:11:29     105
2017:11:30     189
2017:12:01      42
2017:12:04     168
2017:12:05      84
2017:12:06     209
2017:12:07     210
2017:12:08     252
2017:12:09    2835
2018:03:24     189
2018:03:26     357
2018:03:27     502
2018:04:02     147
2018:04:05      63
2018:04:08      84
2018:04:16      21
2018:04:24      21
Length: 76, dtype: int64

In [279]:
# number of unique MM/YY of filming
df_61.groupby(df_61.gps_date_time.str[:7]).size()

gps_date_time
2018:02    1616
2018:03      42
2018:04    2121
2018:05    3671
2018:06    5287
2018:07    5345
2018:08    7028
2018:09    3776
2018:10    2917
2018:11    6688
2018:12    2746
2019:01    2016
2019:02     543
2019:03    3356
dtype: int64

In [83]:
# plotting the total number of driving hours
driver_ids = [61, 107, 89, 69, 39, 91, 103, 65, 97, 47, 37, 31, 45, 87, 95, 32, 
              43, 29, 21, 19, 67, 105, 33, 17, 35, 6, 48, 23, 63, 22, 109, 41, 13, 25, 59, 96, 75]

id_dfs = []
for id_number in driver_ids:
    id_dfs.append(pd.DataFrame(df_copy[df_copy.driver_id == id_number]))

# hours = id_dfs[3].gps_date_time.str[11:13].tolist()
# days = id_dfs[3].gps_date_time.str[:10].tolist()

# hour_df = pd.DataFrame(id_dfs[3].groupby([id_dfs[3].gps_date_time.str[:10], id_dfs[3].gps_date_time.str[11:13]]).size())


# sum1 = hour_df.groupby(["gps_date_time"]).size().sum(level=0)
# res = 0
# for i in range(len(sum1)):
#     res += sum1[i]
# print(res)

for id_df in id_dfs[32:33]:
    hour_df = pd.DataFrame(id_df.groupby([id_df.gps_date_time.str[:10], id_df.gps_date_time.str[11:13]]).size())
    print(hour_df)
    sum1 = hour_df.groupby(["gps_date_time"]).size()
    res = 0
    for i in range(len(sum1)):
        res += sum1[i]
    print(res)


#     table = id_df.gps_date_time.str[11:13].tolist()
#     hour_dict = {}
#     for hour in table:
#         if hour not in hour_dict:
#             hour_dict[hour] = 1
#     print(len(hour_dict))

                               0
gps_date_time gps_date_time     
2019:05:24    04             378
              05             168
2019:05:29    05             504
3


In [345]:
geolocator = Nominatim()
location = geolocator.reverse("52.509669, 13.376294")
print(location.address)

/home/an/anaconda2/lib/python2.7/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Using Nominatim with the default "geopy/1.20.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  """Entry point for launching an IPython kernel.


GeocoderUnavailable: Service not available

In [343]:
# scene statistics
# dictionaries keeping track of the number of scenes, clips, and samples for each subcategory in lighting, weather, and scenery

for df in [df_61, df_107, df_89]:
    titles = []
    data = df
    sample_count = len(data.index)

    clip_count = data.groupby(["filename"]).size()
    
    uniq_name = set()
    
    for name in data['filename']:      
        title = name[:-10]
        new = re.split(r'[\s-]+', title)
        if new not in titles:
            titles.append(new)
#         for descr in new:
#             uniq_name.add(descr)

    light_dict = {}
    weather_dict = {}
    loc_dict = {}
    
    for name in titles:
        
        if len(name) == 1:
            loc_dict[name[0]] = len(data[data['filename'].str.contains(name[0])])
            light_dict["none"] = len(data[data['filename'].str.contains(name[0])])
            weather_dict["none"] = len(data[data['filename'].str.contains(name[0])])
            continue
 
        light = name[0]
        weather = name[1]
        loc = name[2]
        
        if light not in light_dict:
            light_dict[light] = len(data[data['filename'].str.contains(light)])

        if weather not in weather_dict:
            weather_dict[weather] = len(data[data['filename'].str.contains(weather)])

        if loc not in loc_dict:
            loc_dict[loc] = len(data[data['filename'].str.contains(loc)])

    print(light_dict)
    print(weather_dict)
    print(loc_dict)
    print('##############')

{'none': 815, 'day': 32999, 'dawn_or_dusk': 1844, 'night': 11494}
{'none': 815, 'snowy': 3673, 'clear': 6185, 'overcast': 4384, 'sunny': 10724, 'heavy_rain': 3144, 'partly_cloudy': 12502, 'light_rain': 5011, 'foggy': 714}
{'country_side': 168, 'gas_station': 231, 'tunnel': 815, 'suburban': 9753, 'forest_road': 294, 'city_center': 30330, 'parking_lot': 252, 'highway': 5309}
##############
{'none': 1973, 'day': 25234, 'dawn_or_dusk': 2344, 'night': 5124}
{'none': 1973, 'snowy': 2409, 'clear': 4264, 'overcast': 6104, 'sunny': 8185, 'heavy_rain': 1332, 'partly_cloudy': 6923, 'light_rain': 3380, 'foggy': 105}
{'country_side': 7422, 'gas_station': 574, 'tunnel': 1973, 'suburban': 5950, 'forest_road': 2288, 'city_center': 7008, 'parking_lot': 1253, 'highway': 8207}
##############
{'none': 2511, 'day': 10630, 'dawn_or_dusk': 491, 'night': 2301}
{'none': 2511, 'snowy': 2667, 'clear': 1755, 'overcast': 1602, 'sunny': 3167, 'heavy_rain': 588, 'partly_cloudy': 2016, 'light_rain': 1197, 'foggy': 43

In [106]:
# gps speed buckets 
pd.options.display.max_rows = 3000

df_107.head(300)

filename  driver_id  video_time(s)  \
168  day-overcast-forest_road-00006.mov        107              0   
169  day-overcast-forest_road-00006.mov        107              1   
170  day-overcast-forest_road-00006.mov        107              2   
171  day-overcast-forest_road-00006.mov        107              3   
172  day-overcast-forest_road-00006.mov        107              4   
173  day-overcast-forest_road-00006.mov        107              5   
174  day-overcast-forest_road-00006.mov        107              6   
175  day-overcast-forest_road-00006.mov        107              7   
176  day-overcast-forest_road-00006.mov        107              8   
177  day-overcast-forest_road-00006.mov        107              9   
178  day-overcast-forest_road-00006.mov        107             10   
179  day-overcast-forest_road-00006.mov        107             11   
180  day-overcast-forest_road-00006.mov        107             12   
181  day-overcast-forest_road-00006.mov        107             13   
182  day-overcast-forest_road-00006.mov        107             14   
183  day-overcast-forest_road-00006.mov        107             15   
184  day-overcast-forest_road-00006.mov        107             16   
185  day-overcast-forest_road-00006.mov        107             17   
186  day-overcast-forest_road-00006.mov        107             18   
187  day-overcast-forest_road-00006.mov        107             19   
188  day-overcast-forest_road-00006.mov        107             20   
189  day-overcast-forest_road-00007.mov        107              0   
190  day-overcast-forest_road-00007.mov        107              1   
191  day-overcast-forest_road-00007.mov        107              2   
192  day-overcast-forest_road-00007.mov        107              3   
193  day-overcast-forest_road-00007.mov        107              4   
194  day-overcast-forest_road-00007.mov        107              5   
195  day-overcast-forest_road-00007.mov        107              6   
196  day-overcast-forest_road-00007.mov        107              7   
197  day-overcast-forest_road-00007.mov        107              8   
198  day-overcast-forest_road-00007.mov        107              9   
199  day-overcast-forest_road-00007.mov        107             10   
200  day-overcast-forest_road-00007.mov        107             11   
201  day-overcast-forest_road-00007.mov        107             12   
202  day-overcast-forest_road-00007.mov        107             13   
203  day-overcast-forest_road-00007.mov        107             14   
204  day-overcast-forest_road-00007.mov        107             15   
205  day-overcast-forest_road-00007.mov        107             16   
206  day-overcast-forest_road-00007.mov        107             17   
207  day-overcast-forest_road-00007.mov        107             18   
208  day-overcast-forest_road-00007.mov        107             19   
209  day-overcast-forest_road-00007.mov        107             20   
378  day-overcast-forest_road-00016.mov        107              0   
379  day-overcast-forest_road-00016.mov        107              1   
380  day-overcast-forest_road-00016.mov        107              2   
381  day-overcast-forest_road-00016.mov        107              3   
382  day-overcast-forest_road-00016.mov        107              4   
383  day-overcast-forest_road-00016.mov        107              5   
384  day-overcast-forest_road-00016.mov        107              6   
385  day-overcast-forest_road-00016.mov        107              7   
386  day-overcast-forest_road-00016.mov        107              8   
387  day-overcast-forest_road-00016.mov        107              9   
388  day-overcast-forest_road-00016.mov        107             10   
389  day-overcast-forest_road-00016.mov        107             11   
390  day-overcast-forest_road-00016.mov        107             12   
391  day-overcast-forest_road-00016.mov        107             13   
392  day-overcast-forest_road-00016.mov        107             14   
393  day-overcast-forest_road

In [101]:
df_13 = pd.DataFrame(df_copy[df_copy.driver_id == 13])
pd.options.display.max_rows = 1050

df_13.head(5)

filename  driver_id  video_time(s)  \
145696  night-light_rain-forest_road-00003.mov         13              0   
145697  night-light_rain-forest_road-00003.mov         13              1   
145698  night-light_rain-forest_road-00003.mov         13              2   
145699  night-light_rain-forest_road-00003.mov         13              3   
145700  night-light_rain-forest_road-00003.mov         13              4   

               gps_date_time         gps_latitude         gps_longitude  \
145696  2019:05:24 04:50:35Z  44 deg 12' 32.49" N  121 deg 13' 20.31" W   
145697  2019:05:24 04:50:36Z  44 deg 12' 33.35" N  121 deg 13' 19.64" W   
145698  2019:05:24 04:50:37Z  44 deg 12' 34.21" N  121 deg 13' 18.98" W   
145699  2019:05:24 04:50:38Z  44 deg 12' 35.05" N  121 deg 13' 18.33" W   
145700  2019:05:24 04:50:39Z  44 deg 12' 35.89" N  121 deg 13' 17.67" W   

        gps_speed(km/h)  
145696          109.044  
145697          109.188  
145698          108.072  
145699          107.892  
145700          106.848

In [112]:
# speed threshold distribution
speeds = df["gps_speed(km/h)"].tolist()
speed_dict = {'x < 0.5': 0, '0.5 <= x < 10.0': 0, '10.0 <= x': 0, '0.00': 0}
for speed in speeds:
    if speed < 0.5 and speed != 0:
        speed_dict['x < 0.5'] += 1
    elif speed >= 10:
        speed_dict['10.0 <= x'] += 1
    elif speed == 0:
        speed_dict['0.00'] += 1
    else:
        speed_dict['0.5 <= x < 10.0'] += 1
print(speed_dict)

{'0.5 <= x < 10.0': 20609, 'x < 0.5': 7832, '0.00': 8236, '10.0 <= x': 160687}


In [111]:
speeds = df["gps_speed(km/h)"].tolist()
sd = {'0.00': 0, '(0.0, 0.5)': 0, '[0.5-10.0)': 0, '[10.0, 20.0)': 0, '[20.0, 30.0)': 0,
      "[30.0, 40.0)": 0, "[40.0, 50.0)": 0, "[50.0, 60.0)": 0, "[60.0, 70.0)": 0,
      "[70.0, 80.0)": 0, "[80.0, 90.0)": 0, "[90.0, 100.0)": 0, "[100.0, 110.0)": 0, 
      "[110.0, 120.0)": 0, "[120.0, inf)": 0}
for speed in speeds:
    if speed == 0:
        sd['0.00'] += 1
    elif speed < 0.5:
        sd['(0.0, 0.5)'] += 1
    elif 0.5 <= speed < 10:
        sd['[0.5-10.0)'] += 1
    elif 10 <= speed < 20:
        sd['[10.0, 20.0)'] += 1
    elif 20 <= speed < 30:
        sd['[20.0, 30.0)'] += 1
    elif 30 <= speed < 40:
        sd["[30.0, 40.0)"] += 1
    elif 40 <= speed < 50:
        sd["[40.0, 50.0)"] += 1
    elif 50 <= speed < 60:
        sd["[50.0, 60.0)"] += 1
    elif 60 <= speed < 70:
        sd["[60.0, 70.0)"] += 1
    elif 70 <= speed < 80:
        sd["[70.0, 80.0)"] += 1
    elif 80 <= speed < 90:
        sd["[80.0, 90.0)"] += 1
    elif 90 <= speed < 100:
        sd["[90.0, 100.0)"] += 1
    elif 100 <= speed < 110:
        sd["[100.0, 110.0)"] += 1
    elif 110 <= speed < 120:
        sd[ "[110.0, 120.0)"] += 1
    else:
        sd["[120.0, inf)"] += 1

for i, val in sd.items():
    print (i, val)

('[40.0, 50.0)', 14050)
('[10.0, 20.0)', 26280)
('[20.0, 30.0)', 31257)
('[90.0, 100.0)', 9540)
('[0.5-10.0)', 20609)
('[100.0, 110.0)', 10928)
('[60.0, 70.0)', 8422)
('0.00', 8236)
('[50.0, 60.0)', 9802)
('[120.0, inf)', 2064)
('[80.0, 90.0)', 7633)
('[110.0, 120.0)', 8238)
('[70.0, 80.0)', 7802)
('(0.0, 0.5)', 7832)
('[30.0, 40.0)', 24671)


In [33]:
# per clip median and minimum gps speed
speed_df = pd.DataFrame(df.groupby([df['filename'], df["gps_speed(km/h)"]]).size())
speed_df

clip_list = df['filename'].tolist()
clip_set = set(clip_list)

clip_dfs = []
for clip in clip_set:
    clip_df = clip_dfs.append(pd.DataFrame(df_copy[df_copy.filename == clip]))

for clip_df in clip_dfs[:10]:
    clip_df['gps_speed(km/h)'].median()

TypeError: 'set' object has no attribute '__getitem__'

In [98]:
table = df.groupby('filename')['gps_speed(km/h)']
clip_list = df['filename'].tolist()
clip_set = set(clip_list)

count = 0

for clip in clip_set:
    speeds = table.get_group(clip)
    med = median(speeds)
    maxx = max(speeds)
    avg = mean(speeds)
#     print(maxx)
    if med == 0:
        count += 1
#         try:
#             print(avg)
#             print(re.split(r'[\s-]+', clip[:-3]))
            
#         except:
#             pass
        


In [21]:
# find counts for each category
pd.options.display.max_rows = 10000
df.groupby([df.filename.str[:-10], df.filename.str[-9:]]).size()
# df.groupby([df.gps_date_time.str[:4], df.filename]).size()

filename                                 filename 
dawn_or_dusk-heavy_rain-city_center      00001.mov    21
                                         00002.mov    21
                                         00003.mov    21
                                         00004.mov    21
                                         00005.mov    21
                                         00006.mov    21
                                         00007.mov    21
                                         00008.mov    21
                                         00009.mov    21
dawn_or_dusk-heavy_rain-country_side     00001.mov    21
                                         00002.mov    21
                                         00003.mov    21
dawn_or_dusk-heavy_rain-forest_road      00001.mov    21
                                         00002.mov    21
                                         00003.mov    21
dawn_or_dusk-heavy_rain-gas_station      00001.mov    21
                                     

In [20]:
category_df = pd.DataFrame(df.groupby([df.filename.str[:-10], df.filename.str[-9:]])).size()

TypeError: 'numpy.int64' object is not callable